### Camada Gold (Delta): Criação de Fatos e Dimensões

In [0]:
from pyspark.sql import SparkSession

# Create a SparkSession with the required configurations for Delta Lake
spark = SparkSession.builder \
  .appName("Carga Delta") \
  .config("spark.sql.extensions", "io.delta.sql.DeltaSparkSessionExtension") \
  .config("spark.catalog.spark_catalog", "org.apache.spark.sql.delta.catalog.DeltaCatalog") \
  .getOrCreate()

**Importando o SparkSession**
- **SparkSession**: O ponto de entrada para interagir com o Spark, utilizado para criar DataFrames e realizar operações de consulta, escrita e leitura.

**Criando a Sessão do Spark**
- **SparkSession.builder**: Inicia a construção de uma sessão do Spark.
- **.appName("Carga Delta")**: Define o nome do aplicativo Spark como **"Carga Delta"**, o que é útil para identificar o job em logs e no UI do Spark.

**Habilitando o Suporte ao Delta Lake**
- **"spark.sql.extensions"**: Adiciona a extensão **DeltaSparkSessionExtension** que habilita o suporte ao Delta Lake no Spark. O Delta Lake é uma camada de armazenamento transacional que adiciona ACID (Atomicidade, Consistência, Isolamento e Durabilidade) a dados armazenados em formato Parquet no Spark.
- **"spark.catalog.spark_catalog"**: Configura o DeltaCatalog, que permite ao Spark lidar com tabelas Delta por meio do catálogo de metadados. Isso possibilita que as operações de leitura/escrita em Delta sejam tratadas da mesma forma que em tabelas Spark SQL tradicionais.

In [0]:
# Define os caminhos de armazenamento no Data Lake
silver_path = "/mnt/lhdw/silver/vendas"
gold_path = "/mnt/lhdw/gold/vendas_delta"

### Ler dados Camada Silver

In [0]:
# Lendo os dados da camada Silver no formato Parquet
df_silver = spark.read.format("parquet").load(silver_path)

**Lendo os Dados da Camada Silver**
- Lê os dados da camada Silver, que estão armazenados no formato Parquet, criando o DataFrame **df_silver**. O caminho **silver_path** é o local onde os dados Parquet da camada Silver estão armazenados.

### Criação da Dimensão Produto

In [0]:
from pyspark.sql.functions import monotonically_increasing_id

# Definindo a tabela de destino na camada Gold
tb_destino = "dim_produto"

# Selecionando as colunas necessárias para a tabela de dimensões de produto e removendo duplicatas
dim_produto_df = df_silver.select(
  "IDProduto", "Produto", "Categoria").dropDuplicates()

#  Adiciona uma nova coluna chamada sk_produto, que será a chave surrogate (chave substituta)que gera IDs únicos, começando em 1
dim_produto_df = dim_produto_df.withColumn("sk_produto", monotonically_increasing_id()+1)

# Gravando os dados no formato Delta na camada Gold
dim_produto_df.write.format("delta").mode("overwrite").save(f"{gold_path}/{tb_destino}")

display(dim_produto_df)
dim_produto_df.count()

IDProduto Produto Categoria sk_produto 585 Maximus UC-50 Urban 1 423 Maximus UM-28 Urban 2 562 Maximus UC-27 Youth 3 405 Maximus UM-10 Accessory 4 540 Maximus UC-05 Mix 5 681 Maximus UC-46 Urban 6 628 Maximus UC-93 Urban 7 415 Maximus UM-20 Urban 8 406 Maximus UM-11 Accessory 9 512 Maximus UR-01 Urban 10 525 Maximus UE-13 Urban 11 520 Maximus UE-08 Urban 12 609 Maximus UC-74 Urban 13 528 Maximus UE-16 Urban 14 686 Maximus UC-51 Urban 15 517 Maximus UE-05 Urban 16 662 Maximus UC-27 Urban 17 501 Maximus UM-06 Urban 18 577 Maximus UC-42 Urban 19 538 Maximus UC-03 Mix 20 537 Maximus UC-02 Mix 21 578 Maximus UC-43 Urban 22 690 Maximus UC-55 Urban 23 515 Maximus UE-03 Urban 24 579 Maximus UC-44 Urban 25 438 Maximus UM-43 Urban 26 638 Maximus UC-03 Urban 27 524 Maximus UE-12 Urban 28 684 Maximus UC-49 Urban 29 689 Maximus UC-54 Urban 30 685 Maximus UC-50 Urban 31 443 Maximus UM-48 Urban 32 636 Maximus UC-01 Urban 33 420 Maximus UM-25 Urban 34 416 Maximus UM-21 Urban 35 657 Maximus UC-22 Urban 36 559 Maximus UC-24 Mix 37 424 Maximus UM-29 Urban 38 539 Maximus UC-04 Mix 39 457 Maximus UM-62 Urban 40 541 Maximus UC-06 Mix 41 491 Maximus UM-96 Urban 42 470 Maximus UM-75 Urban 43 599 Maximus UC-64 Urban 44 601 Maximus UC-66 Urban 45 548 Maximus UC-13 Mix 46 394 Maximus RS-01 Rural 47 572 Maximus UC-37 Youth 48 635 Maximus UC-00 Urban 49 605 Maximus UC-70 Urban 50 674 Maximus UC-39 Urban 51 580 Maximus UC-45 Urban 52 473 Maximus UM-78 Urban 53 568 Maximus UC-33 Youth 54 427 Maximus UM-32 Urban 55 567 Maximus UC-32 Youth 56 604 Maximus UC-69 Urban 57 687 Maximus UC-52 Urban 58 492 Maximus UM-97 Urban 59 611 Maximus UC-76 Urban 60 545 Maximus UC-10 Mix 61 478 Maximus UM-83 Urban 62 535 Maximus UE-23 Urban 63 596 Maximus UC-61 Urban 64 691 Maximus UC-56 Urban 65 627 Maximus UC-92 Urban 66 527 Maximus UE-15 Urban 67 639 Maximus UC-04 Urban 68 523 Maximus UE-11 Urban 69 625 Maximus UC-90 Urban 70 516 Maximus UE-04 Urban 71 404 Maximus UM-09 Accessory 72 504 Maximus UM-09 Urban 73 675 Maximus UC-40 Urban 74 407 Maximus UM-12 Accessory 75 506 Maximus UM-11 Urban 76 626 Maximus UC-91 Urban 77 629 Maximus UC-94 Urban 78 449 Maximus UM-54 Urban 79 660 Maximus UC-25 Urban 80 531 Maximus UE-19 Urban 81 544 Maximus UC-09 Mix 82 583 Maximus UC-48 Urban 83 650 Maximus UC-15 Urban 84 546 Maximus UC-11 Mix 85 426 Maximus UM-31 Urban 86 592 Maximus UC-57 Urban 87 534 Maximus UE-22 Urban 88 556 Maximus UC-21 Mix 89 655 Maximus UC-20 Urban 90 590 Maximus UC-55 Urban 91 672 Maximus UC-37 Urban 92 430 Maximus UM-35 Urban 93 659 Maximus UC-24 Urban 94 633 Maximus UC-98 Urban 95 593 Maximus UC-58 Urban 96 433 Maximus UM-38 Urban 97 554 Maximus UC-19 Mix 98 549 Maximus UC-14 Mix 99 676 Maximus UC-41 Urban 100 440 Maximus UM-45 Urban 101 615 Maximus UC-80 Urban 102 603 Maximus UC-68 Urban 103 600 Maximus UC-65 Urban 104 429 Maximus UM-34 Urban 105 588 Maximus UC-53 Urban 106 412 Maximus UM-17 Urban 107 487 Maximus UM-92 Urban 108 499 Maximus UM-04 Urban 109 456 Maximus UM-61 Urban 110 496 Maximus UM-01 Urban 111 400 Maximus UM-05 Accessory 112 553 Maximus UC-18 Mix 113 529 Maximus UE-17 Urban 114 489 Maximus UM-94 Urban 115 533 Maximus UE-21 Urban 116 419 Maximus UM-24 Urban 117 495 Maximus UM-00 Urban 118 532 Maximus UE-20 Urban 119 565 Maximus UC-30 Youth 120 481 Maximus UM-86 Urban 121 436 Maximus UM-41 Urban 122 569 Maximus UC-34 Youth 123 409 Maximus UM-14 Urban 124 648 Maximus UC-13 Urban 125 581 Maximus UC-46 Urban 126 418 Maximus UM-23 Urban 127 475 Maximus UM-80 Urban 128 503 Maximus UM-08 Urban 129 641 Maximus UC-06 Urban 130 510 Maximus UM-15 Urban 131 497 Maximus UM-02 Urban 132 459 Maximus UM-64 Urban 133 425 Maximus UM-30 Urban 134 530 Maximus UE-18 Urban 135 445 Maximus UM-50 Urban 136 396 Maximus UM-01 Accessory 137

Out[4]: 137

**Importando a Função monotonically_increasing_id**
- **monotonically_increasing_id()**: Esta função gera um ID único (número inteiro crescente) para cada linha, usado aqui como uma chave substituta (surrogate key). É útil quando você precisa adicionar um identificador único para cada registro.

**Definindo a Tabela de Destino**
- O nome da tabela de destino é definido como **dim_produto**, o que sugere que os dados são destinados para uma tabela de dimensões que contém informações sobre produtos. Dimensões são usadas em modelagem dimensional para apoiar análises OLAP.

**Selecionando Colunas Necessárias e Removendo Duplicatas**
- select("IDProduto", "Produto", "Categoria")**: Seleciona apenas as colunas relacionadas ao produto, que serão armazenadas na tabela de dimensões.
- **.dropDuplicates()**: Remove linhas duplicadas com base nas colunas selecionadas. Isso garante que cada produto seja único na tabela de dimensões.

**Adicionando uma Chave Surrogate (sk_produto)**
- **.withColumn("sk_produto", ...)**: Adiciona uma nova coluna chamada **sk_produto**, que será a chave surrogate (chave substituta).
- **monotonically_increasing_id() + 1**: Gera IDs únicos, começando em 1. As surrogate keys são usadas em tabelas de dimensões para garantir que cada registro tenha um identificador exclusivo, que não depende da chave natural (neste caso, **IDProduto**).

**Gravando os Dados no Formato Delta**
- **.write**: Inicia a operação de escrita no DataFrame **dim_produto_df**.
- **.format("delta")**: Especifica que os dados serão gravados no formato Delta, que suporta transações ACID e versionamento de dados.
- **.mode("overwrite")**: Usa o modo de sobrescrita. Se a tabela já existir no local **gold_path/dim_produto**, ela será sobrescrita.
- **.save(f"{gold_path}/{tb_destino}")**: Salva os dados no caminho especificado em **gold_path**, criando a tabela de dimensões **dim_produto** na camada Gold.

### Criação da Dimensão Categoria

In [0]:
from pyspark.sql.functions import monotonically_increasing_id

# Definindo a tabela de destino na camada Gold
tb_destino = "dim_categoria"

# Selecionando as colunas necessárias para a tabela de dimensões de categoria e removendo duplicatas
dim_categoria_df = df_silver.select(
  "Categoria").dropDuplicates()

#  Adiciona uma nova coluna chamada sk_categoria, que será a chave surrogate (chave substituta)que gera IDs únicos, começando em 1
dim_categoria_df = dim_categoria_df.withColumn("sk_categoria", monotonically_increasing_id()+1)

# Gravando os dados no formato Delta na camada Gold
dim_categoria_df.write.format("delta").mode("overwrite").save(f"{gold_path}/{tb_destino}")

display(dim_categoria_df)
dim_categoria_df.count()

Categoria sk_categoria Mix 1 Urban 2 Youth 3 Accessory 4 Rural 5

Out[5]: 5

### Criação da Dimensão Segmento

In [0]:
from pyspark.sql.functions import monotonically_increasing_id

# Definindo a tabela de destino na camada Gold
tb_destino = "dim_segmento"

# Selecionando as colunas necessárias para a tabela de dimensões de segmento e removendo duplicatas
dim_segmento_df = df_silver.select(
  "Segmento").dropDuplicates()

#  Adiciona uma nova coluna chamada sk_segmento, que será a chave surrogate (chave substituta)que gera IDs únicos, começando em 1
dim_segmento_df = dim_segmento_df.withColumn("sk_segmento", monotonically_increasing_id()+1)

# Gravando os dados no formato Delta na camada Gold
dim_segmento_df.write.format("delta").mode("overwrite").save(f"{gold_path}/{tb_destino}")

display(dim_segmento_df)
dim_segmento_df.count()

Segmento sk_segmento All Season 1 Extreme 2 Youth 3 Accessory 4 Select 5 Productivity 6 Regular 7 Convenience 8 Moderation 9

Out[6]: 9

### Criação da Dimensão Fabricante

In [0]:
from pyspark.sql.functions import monotonically_increasing_id

# Definindo a tabela de destino na camada Gold
tb_destino = "dim_fabricante"

# Selecionando as colunas necessárias para a tabela de dimensões de fabricante e removendo duplicatas
dim_fabricante_df = df_silver.select(
  "IDFabricante", "Fabricante").dropDuplicates()

#  Adiciona uma nova coluna chamada sk_fabricante, que será a chave surrogate (chave substituta)que gera IDs únicos, começando em 1
dim_fabricante_df = dim_fabricante_df.withColumn("sk_fabricante", monotonically_increasing_id()+1)

# Gravando os dados no formato Delta na camada Gold
dim_fabricante_df.write.format("delta").mode("overwrite").save(f"{gold_path}/{tb_destino}")

display(dim_fabricante_df)
dim_fabricante_df.count()

IDFabricante Fabricante sk_fabricante 7 VanArsdel 1

Out[7]: 1

### Criação da Dimensão Geografia

In [0]:
from pyspark.sql.functions import monotonically_increasing_id

# Definindo a tabela de destino na camada Gold
tb_destino = "dim_geografia"

# Selecionando as colunas necessárias para a tabela de dimensões de geografia e removendo duplicatas
dim_geografia_df = df_silver.select(
  "Cidade", "Estado", "Regiao", "Distrito", "Pais", "CodigoPostal").dropDuplicates()

#  Adiciona uma nova coluna chamada sk_geografia, que será a chave surrogate (chave substituta)que gera IDs únicos, começando em 1
dim_geografia_df = dim_geografia_df.withColumn("sk_geografia", monotonically_increasing_id()+1)

# Gravando os dados no formato Delta na camada Gold
dim_geografia_df.write.format("delta").mode("overwrite").save(f"{gold_path}/{tb_destino}")

display(dim_geografia_df)
dim_geografia_df.count()

Cidade Estado Regiao Distrito Pais CodigoPostal sk_geografia Batavia IL Central District #31 USA 60510 1 Denver CO Central District #20 USA 80232 2 Nampa ID West District #33 USA 83651 3 Belmar NJ East District #04 USA 7719 4 Mount Dora FL East District #12 USA 32757 5 Moses Lake WA West District #33 USA 98837 6 Indio CA West District #38 USA 92203 7 Jacksonville FL East District #12 USA 32225 8 Warrenton MO Central District #29 USA 63383 9 Crosby TX Central District #23 USA 77532 10 Bakersfield CA West District #38 USA 93390 11 Flossmoor IL Central District #31 USA 60422 12 Sebastian FL East District #10 USA 32958 13 Greenfield MA East District #02 USA 1301 14 Chesapeake VA East District #07 USA 23323 15 Kissimmee FL East District #12 USA 34747 16 Jefferson TX Central District #24 USA 75657 17 Seabrook TX Central District #23 USA 77586 18 Las Cruces NM West District #39 USA 88001 19 Paris KY East District #16 USA 40361 20 East Lyme CT East District #02 USA 6333 21 New London MN Central District #32 USA 56273 22 Smithfield NC East District #08 USA 27577 23 Carencro LA Central District #24 USA 70520 24 Saint Louis MO Central District #29 USA 63125 25 Colorado Springs CO Central District #20 USA 80921 26 Wilmington OH East District #16 USA 45177 27 Pawtucket RI East District #02 USA 2861 28 Irvine CA West District #37 USA 92606 29 Sioux City IA Central District #32 USA 51106 30 Milledgeville GA East District #09 USA 31061 31 Coldwater MS Central District #25 USA 38618 32 Jefferson WI Central District #26 USA 53549 33 Fort Knox KY East District #16 USA 40121 34 Queen Anne MD East District #05 USA 21657 35 Lawson MO Central District #30 USA 64062 36 Baton Rouge LA Central District #24 USA 70803 37 Arcadia WI Central District #27 USA 54612 38 Prosper TX Central District #22 USA 75078 39 Pikesville MD East District #05 USA 21208 40 White Stone VA East District #07 USA 22578 41 Topeka KS Central District #30 USA 66611 42 Carlisle KY East District #16 USA 40311 43 New Egypt NJ East District #04 USA 8533 44 Florence SC East District #11 USA 29506 45 Oakland Gardens NY East District #03 USA 11364 46 Ottawa IL Central District #27 USA 61350 47 Kokomo IN East District #17 USA 46902 48 South Bend IN East District #17 USA 46628 49 Greer SC East District #11 USA 29651 50 Delanson NY East District #01 USA 12053 51 San Antonio TX Central District #23 USA 78266 52 Titusville PA East District #13 USA 16354 53 Racine WI Central District #31 USA 53403 54 Sherburn MN Central District #28 USA 56171 55 West Alexandria OH East District #16 USA 45381 56 Bigfork MT West District #33 USA 59911 57 Brandon MN Central District #32 USA 56315 58 Lowell IN Central District #31 USA 46356 59 Oil City PA East District #13 USA 16301 60 Lees Summit MO Central District #30 USA 64081 61 Woodlawn IL Central District #25 USA 62898 62 Naples FL East District #10 USA 34104 63 Owego NY East District #01 USA 13827 64 Sewell NJ East District #04 USA 8080 65 Ridgway PA East District #13 USA 15853 66 Roswell NM Central District #22 USA 88201 67 Castle Rock CO Central District #20 USA 80104 68 Antigo WI Central District #26 USA 54409 69 Wichita KS Central District #21 USA 67219 70 San Antonio TX Central District #23 USA 78210 71 Scio NY East District #06 USA 14880 72 Pewee Valley KY East District #16 USA 40056 73 Canton OH East District #14 USA 44718 74 Dendron VA East District #07 USA 23839 75 Lenoir City TN East District #19 USA 37771 76 Camillus NY East District #01 USA 13031 77 Wellington OH East District #14 USA 44090 78 Damascus OR West District #34 USA 97089 79 Clovis CA West District #36 USA 93612 80 Atascadero CA West District #37 USA 93422 81 Park Hills MO Central District #29 USA 63601 82 Lawton MI East District #18 USA 49065 83 Noblesville IN East District #17 USA 46060 84 Philadelphia PA East District #04 USA 19116 85 Lewiston MN Central District #28 USA 55952 86 Monroe LA Central District #24 USA 71202 87 Preston CT East District #02 USA 6365 88 Storm Lake IA Cen

Out[8]: 20467

### Criação da Dimensão Cliente

In [0]:
from pyspark.sql.functions import col, monotonically_increasing_id

# Definindo a tabela de destino como "dim_cliente"
tb_destino = "dim_cliente"

# Selecionando colunas relevantes de cliente e removendo duplicatas
dim_cliente_df = df_silver.select(
  "IDCliente", "Nome", "Email", "Cidade", "Estado", "Regiao", "Distrito", "Pais", "CodigoPostal"
).dropDuplicates()

# Realizando um join para associar geografia com base nos atributos geográficos
dim_cliente_com_sk_df = dim_cliente_df.alias("cliente") \
    .join(dim_geografia_df.alias("geografia"), 
          (col("cliente.Cidade") == col("geografia.Cidade")) &
          (col("cliente.Estado") == col("geografia.Estado")) &
          (col("cliente.Regiao") == col("geografia.Regiao")) &
          (col("cliente.Distrito") == col("geografia.Distrito")) &
          (col("cliente.Pais") == col("geografia.Pais")) &
          (col("cliente.CodigoPostal") == col("geografia.CodigoPostal")), 
          "left") \
    .select("cliente.IDCliente", "cliente.Nome", "cliente.Email", "geografia.sk_geografia")

# Adicionando uma chave surrogate para o cliente
dim_cliente_com_sk_df = dim_cliente_com_sk_df.withColumn("sk_cliente", monotonically_increasing_id()+1)

# Selecionando as colunas necessárias com as chaves surrogate
dim_cliente_com_sk_df = dim_cliente_com_sk_df.select("IDCliente", "Nome", "Email", "sk_geografia", "sk_cliente")

# Salvando a tabela de dimensão de cliente no formato Delta na camada Gold
dim_cliente_com_sk_df.write.format("delta").mode("overwrite").save(f"{gold_path}/{tb_destino}")

display(dim_cliente_com_sk_df)
dim_cliente_com_sk_df.count()

IDCliente Nome Email sk_geografia sk_cliente 255010 John Trevino john.trevino@xyza.com 3468 1 272755 Kameko Langley kameko.langley@xyza.com 8589941780 2 111898 Rogan Saunders rogan.saunders@xyza.com 153 3 8933 Jackson Levy jackson.levy@xyza.com 4822 4 88529 Ignacia Jacobson ignacia.jacobson@xyza.com 6282 5 141432 Tanya Whitley tanya.whitley@xyza.com 4 6 151370 Kaden Washington kaden.washington@xyza.com 8589938460 7 45239 Tara Sloan tara.sloan@xyza.com 8589942604 8 5562 Moses Carney moses.carney@xyza.com 8589934743 9 106710 Mechelle Watson mechelle.watson@xyza.com 3296 10 147089 Scarlett Acosta scarlett.acosta@xyza.com 8589936209 11 96366 Dieter Moran dieter.moran@xyza.com 1881 12 95624 Dai Wood dai.wood@xyza.com 8589942227 13 118655 Christian Mcleod christian.mcleod@xyza.com 8589939388 14 219399 Karly Green karly.green@xyza.com 5745 15 12194 Cole Eaton cole.eaton@xyza.com 6608 16 814 Autumn Harvey autumn.harvey@xyza.com 8589942658 17 168364 Phillip Bowers phillip.bowers@xyza.com 8589935704 18 240980 Kimberly Wall kimberly.wall@xyza.com 8589936782 19 12195 Josiah Riggs josiah.riggs@xyza.com 6608 20 80883 Fatima Reid fatima.reid@xyza.com 6607 21 17481 Nyssa Cameron nyssa.cameron@xyza.com 8589940764 22 118302 Kermit Olsen kermit.olsen@xyza.com 4103 23 198912 Blaze Gibbs blaze.gibbs@xyza.com 8589942086 24 30571 Joan Mcbride joan.mcbride@xyza.com 8589942364 25 247701 Hedwig Henson hedwig.henson@xyza.com 334 26 158213 Wilma Mcpherson wilma.mcpherson@xyza.com 8589940384 27 116881 Felix Knight felix.knight@xyza.com 8589937512 28 65153 Candace Jensen candace.jensen@xyza.com 5914 29 41050 Orson Mccormick orson.mccormick@xyza.com 8589938096 30 281056 Gage Whitehead gage.whitehead@xyza.com 8589939198 31 190685 Geraldine Ryan geraldine.ryan@xyza.com 8589942236 32 160473 Adria Suarez adria.suarez@xyza.com 8589937573 33 207166 Michelle Woods michelle.woods@xyza.com 8589936646 34 22043 Xavier Lewis xavier.lewis@xyza.com 8589936497 35 277598 Lamar Whitfield lamar.whitfield@xyza.com 4411 36 250670 Ingrid Sandoval ingrid.sandoval@xyza.com 8589936722 37 37983 Aristotle Beach aristotle.beach@xyza.com 5977 38 188503 Barrett Porter barrett.porter@xyza.com 8589941942 39 57355 Kellie Patrick kellie.patrick@xyza.com 6300 40 73204 Jolene Watkins jolene.watkins@xyza.com 8589938774 41 75452 Phoebe Guerra phoebe.guerra@xyza.com 8589936458 42 254726 Theodore Hopper theodore.hopper@xyza.com 8589940321 43 115341 Berk Hines berk.hines@xyza.com 8589937728 44 244467 Ira Wilder ira.wilder@xyza.com 6231 45 265468 Curran Mcintyre curran.mcintyre@xyza.com 8589937069 46 67549 Kai Gilliam kai.gilliam@xyza.com 8589941806 47 19920 Amery Schmidt amery.schmidt@xyza.com 1351 48 26797 Indigo Saunders indigo.saunders@xyza.com 8589938646 49 39511 Suki Barnes suki.barnes@xyza.com 265 50 59074 Palmer Dillon palmer.dillon@xyza.com 8589935324 51 125921 Althea Leach althea.leach@xyza.com 8589939396 52 126229 Arsenio Arnold arsenio.arnold@xyza.com 5457 53 214830 Akeem Bryan akeem.bryan@xyza.com 8589935415 54 264362 Nola Caldwell nola.caldwell@xyza.com 5607 55 196490 Kaitlin Richards kaitlin.richards@xyza.com 8589935359 56 42882 Tatiana Schmidt tatiana.schmidt@xyza.com 3377 57 195458 Stephanie Hawkins stephanie.hawkins@xyza.com 8589941926 58 136124 Mia Bryan mia.bryan@xyza.com 3614 59 143323 Daphne Brock daphne.brock@xyza.com 1489 60 156214 Brendan Schwartz brendan.schwartz@xyza.com 400 61 45868 Daniel Tillman daniel.tillman@xyza.com 2408 62 157371 Buffy Snow buffy.snow@xyza.com 3 63 101803 Kaseem Britt kaseem.britt@xyza.com 8589937496 64 59788 Maya Ramirez maya.ramirez@xyza.com 5978 65 223550 Fatima Gilmore fatima.gilmore@xyza.com 8589935903 66 56525 Wing Wells wing.wells@xyza.com 4392 67 112209 Leonard Potter leonard.potter@xyza.com 4169 68 111562 Conan Griffin conan.griffin@xyza.com 8589935698 69 56524 Kelsey Rios kelsey.rios@xyza.com 4392 70 34403 Dolan Sherman dolan.sherman@xyza.com 6372 71 177317 Virginia Mcgowan virginia.mcgowan@xyza.com 8589935762 72 38274 Fuller Carson full

Out[9]: 112081

**Importando Funções Necessárias**
- **col**: Função usada para acessar colunas no Spark DataFrame.
- **monotonically_increasing_id**: Função usada para gerar IDs únicos crescentes, que serão usados como chaves surrogate (substitutas).

**Definindo a Tabela de Destino**
- Definindo o nome da tabela de destino na camada Gold como **dim_cliente**, o que indica que este DataFrame representa uma dimensão de clientes.

**Selecionando Colunas Relacionadas a Cliente e Removendo Duplicatas**
- Seleciona as colunas que contêm informações de cliente e também atributos geográficos como Cidade, Estado, Região, etc.
- **dropDuplicates()**: Remove registros duplicados para garantir que cada cliente seja único na tabela.

**Realizando o Join para Associar Geografia**
- Realiza um join entre o cliente e a geografia, associando as chaves geográficas (como **Cidade**, **Estado**, **Regiao**, etc.) usando uma combinação de colunas.
- **alias("cliente")** e **alias("geografia")**: Usados para diferenciar as tabelas durante o join.
- **left join**: Um join à esquerda garante que todos os clientes sejam incluídos, mesmo que não tenham correspondência exata em atributos geográficos.

**Adicionando a Chave Surrogate (sk_cliente)**
- Adiciona uma nova coluna chamada sk_cliente que contém uma chave surrogate para cada cliente.
- **monotonically_increasing_id() + 1**: Gera valores crescentes exclusivos para cada registro, começando em 1.

**Selecionando as Colunas Finais**
- Aqui, apenas as colunas necessárias são mantidas: **IDCliente**, **Nome**, **Email**, **sk_geografia** (chave surrogate de geografia) e **sk_cliente** (chave surrogate de cliente).

**Gravando os Dados no Formato Delta**
- Escreve o DataFrame resultante no formato Delta na camada Gold.
- **.format("delta")**: Especifica o formato Delta, que oferece suporte a transações ACID e versionamento.
- **.mode("overwrite")**: Usa o modo overwrite, sobrescrevendo quaisquer dados anteriores que possam existir no caminho especificado.
- **save(f"{gold_path}/{tb_destino}")**: Salva a tabela **dim_cliente** no local da camada Gold (especificado pelo caminho **gold_path**).

### Criação de Tabela Fato

In [0]:
tb_destino = "fato_vendas"

from pyspark.sql.functions import broadcast, year, month

# Realizando os joins com as tabelas de dimensão para criar a tabela fato de vendas
fato_vendas_df = df_silver.alias("s") \
    .join(broadcast(dim_produto_df.select("IDProduto", "sk_produto").alias("dprod")), "IDProduto") \
    .join(broadcast(dim_categoria_df.select("Categoria", "sk_categoria").alias("dcat")), "Categoria") \
    .join(broadcast(dim_segmento_df.select("Segmento", "sk_segmento").alias("dseg")), "Segmento") \
    .join(broadcast(dim_fabricante_df.select("Fabricante", "sk_fabricante").alias("dfab")), "Fabricante") \
    .join(broadcast(dim_cliente_com_sk_df.select("IDCliente", "sk_cliente").alias("dcli")), "IDCliente") \
    .select(
        col("s.Data").alias("DataVenda"),
        "sk_produto",
        "sk_categoria",
        "sk_segmento",
        "sk_fabricante",
        "sk_cliente",
        "Unidades",
        col("s.PrecoUnitario"),
        col("s.CustoUnitario"),
        col("s.TotalVendas")
    )

# Adicionando as colunas de Ano e Mês para particionamento
fato_vendas_df.withColumn("Ano", year("DataVenda")) \
             .withColumn("Mes", month("DataVenda")) \
             .write.format("delta") \
             .mode("overwrite") \
             .option("MaxRecordsPerFile", 1000000) \
             .partitionBy("Ano", "Mes") \
             .save(f"{gold_path}/{tb_destino}")

# Exibindo o DataFrame resultante
display(fato_vendas_df)

# Contando o número total de registros na tabela fato
fato_vendas_df.count()

DataVenda sk_produto sk_categoria sk_segmento sk_fabricante sk_cliente Unidades PrecoUnitario CustoUnitario TotalVendas 2011-04-27 51 2 8 1 25769804455 1 68.24 49.82 68.24 2011-04-02 51 2 8 1 25769805583 1 68.24 49.82 68.24 2011-04-08 51 2 8 1 42949676743 1 68.24 49.82 68.24 2011-04-14 51 2 8 1 42949673877 1 68.24 49.82 68.24 2011-04-24 51 2 8 1 42949673434 1 68.24 49.82 68.24 2011-04-05 51 2 8 1 8589934593 1 68.24 49.82 68.24 2011-04-05 51 2 8 1 42949676956 1 68.24 49.82 68.24 2011-04-22 51 2 8 1 51539609218 1 68.24 49.82 68.24 2011-04-23 51 2 8 1 8589934795 1 68.24 49.82 68.24 2011-04-23 51 2 8 1 51539611716 1 68.24 49.82 68.24 2011-04-25 51 2 8 1 8589937983 1 68.24 49.82 68.24 2011-04-19 51 2 8 1 25769807867 1 68.24 49.82 68.24 2011-04-17 51 2 8 1 8589934796 1 68.24 49.82 68.24 2011-04-13 51 2 8 1 3659 1 68.24 49.82 68.24 2011-04-13 51 2 8 1 51539611717 1 68.24 49.82 68.24 2011-04-21 51 2 8 1 42949675388 1 68.24 49.82 68.24 2011-04-05 51 2 8 1 17179870095 1 68.24 49.82 68.24 2011-04-07 51 2 8 1 60129548272 1 68.24 49.82 68.24 2011-04-14 51 2 8 1 42949676521 1 68.24 49.82 68.24 2011-04-30 51 2 8 1 4126 1 68.24 49.82 68.24 2011-04-08 51 2 8 1 51539611493 1 68.24 49.82 68.24 2011-04-30 51 2 8 1 17179869855 1 68.24 49.82 68.24 2011-04-17 51 2 8 1 487 1 68.24 49.82 68.24 2011-04-01 51 2 8 1 25769806953 1 68.24 49.82 68.24 2011-04-16 51 2 8 1 42949674328 1 68.24 49.82 68.24 2011-04-16 51 2 8 1 2046 1 68.24 49.82 68.24 2011-04-21 51 2 8 1 25769806008 1 68.24 49.82 68.24 2011-04-23 51 2 8 1 34359740659 1 68.24 49.82 68.24 2011-04-27 51 2 8 1 8589939342 1 68.24 49.82 68.24 2011-04-06 51 2 8 1 17179872910 1 68.24 49.82 68.24 2011-04-22 51 2 8 1 25769807188 1 68.24 49.82 68.24 2011-04-30 51 2 8 1 60129546917 1 68.24 49.82 68.24 2011-04-06 51 2 8 1 17179871685 1 68.24 49.82 68.24 2011-04-09 51 2 8 1 60129543572 1 68.24 49.82 68.24 2011-04-09 51 2 8 1 51539609687 1 68.24 49.82 68.24 2011-04-10 51 2 8 1 34359742060 1 68.24 49.82 68.24 2011-04-21 51 2 8 1 51539612418 1 68.24 49.82 68.24 2011-04-21 51 2 8 1 51539610362 1 68.24 49.82 68.24 2011-04-23 51 2 8 1 51539612629 1 68.24 49.82 68.24 2011-04-22 51 2 8 1 60129543089 1 68.24 49.82 68.24 2011-04-30 51 2 8 1 42949674518 1 68.24 49.82 68.24 2011-04-30 51 2 8 1 17179874477 1 68.24 49.82 68.24 2011-04-07 51 2 8 1 42949678085 1 68.24 49.82 68.24 2011-04-23 51 2 8 1 42949673205 1 68.24 49.82 68.24 2011-04-26 51 2 8 1 42949673878 1 68.24 49.82 68.24 2011-04-30 51 2 8 1 34359739297 1 68.24 49.82 68.24 2011-04-08 51 2 8 1 51539608036 1 68.24 49.82 68.24 2011-04-17 51 2 8 1 25769803777 1 68.24 49.82 68.24 2011-04-06 51 2 8 1 17179871244 1 68.24 49.82 68.24 2011-04-20 51 2 8 1 51539607553 1 68.24 49.82 68.24 2011-04-29 51 2 8 1 51539609688 1 68.24 49.82 68.24 2011-04-16 51 2 8 1 60129543347 1 68.24 49.82 68.24 2011-04-27 51 2 8 1 51539608037 1 68.24 49.82 68.24 2011-04-22 51 2 8 1 25769805815 1 68.24 49.82 68.24 2011-04-13 51 2 8 1 945 1 68.24 49.82 68.24 2011-04-08 51 2 8 1 8589937984 1 68.24 49.82 68.24 2011-04-14 51 2 8 1 25769807189 1 68.24 49.82 68.24 2011-04-13 51 2 8 1 17179873141 1 68.24 49.82 68.24 2011-04-27 51 2 8 1 42949676522 1 68.24 49.82 68.24 2011-04-27 51 2 8 1 60129548036 1 68.24 49.82 68.24 2011-04-30 51 2 8 1 60129543573 1 68.24 49.82 68.24 2011-04-21 51 2 8 1 60129543348 1 68.24 49.82 68.24 2011-04-07 51 2 8 1 25769804456 1 68.24 49.82 68.24 2011-04-14 51 2 8 1 42949678086 1 68.24 49.82 68.24 2011-04-06 51 2 8 1 42949674096 1 68.24 49.82 68.24 2011-04-01 51 2 8 1 60129546195 1 68.24 49.82 68.24 2011-04-29 51 2 8 1 25769806483 1 68.24 49.82 68.24 2011-04-14 51 2 8 1 60129544223 1 68.24 49.82 68.24 2011-04-12 51 2 8 1 51539608038 1 68.24 49.82 68.24 2011-04-24 51 2 8 1 51539608730 1 68.24 49.82 68.24 2011-04-26 51 2 8 1 3660 1 68.24 49.82 68.24 2011-04-02 51 2 8 1 1374 1 68.24 49.82 68.24 2011-04-23 51 2 8 1 34359740444 1 68.24 49.82 68.24 2011-04-17 51 2 8 1 8589935688 1 68.24 49.82 68.24 2011-04-23 51 2 8 1 8589937985 1 68.24 49.82 68.24 2011-04-08 51 2 8 1 1797 1 68.24 49.82 

Out[10]: 112202

**Importando Funções Necessárias**
- **broadcast**: Usada para transmitir (broadcast) uma tabela de dimensão menor para otimizar a junção com uma tabela maior (no caso, a tabela de fato).
- **year** e **month**: Funções que extraem o ano e o mês de uma data, usadas para criar colunas adicionais no DataFrame.

**Definindo a Tabela de Destino**
- Aqui, o nome da tabela de destino é definido como **fato_vendas**, que representa a tabela de fatos onde as vendas e as chaves surrogate de várias dimensões serão armazenadas.

**Realizando o Join com as Tabelas de Dimensão**
- **alias("s")**: Apelido dado à tabela de fatos **df_silver** para facilitar o acesso às suas colunas.
- O join é feito entre **df_silver** (fatos de vendas) e as várias dimensões (produto, categoria, segmento, fabricante e cliente) com o uso de **broadcast**. Isso ajuda a otimizar o processo de junção quando as tabelas de dimensão são menores.
- Após o join, o **select** é usado para selecionar as colunas relevantes, como as chaves surrogate (**sk_produto**, **sk_categoria**, etc.) e outras informações de vendas como **Unidades**, **PrecoUnitario**, **CustoUnitario** e **TotalVendas**.

**Adicionando Colunas de Ano e Mês**
- **withColumn("Ano", year("DataVenda"))** e **withColumn("Mes", month("DataVenda"))**: São adicionadas duas novas colunas, **Ano** e **Mês**, extraídas da coluna **DataVenda**, para facilitar a partição dos dados.
- **.write.format("delta")**: Especifica que os dados serão gravados no formato Delta, que suporta transações ACID e versionamento.
- **.mode("overwrite")**: O modo overwrite sobrescreve quaisquer dados existentes no caminho de destino.
- **.option("MaxRecordsPerFile", 1000000)**: Define o máximo de 1 milhão de registros por arquivo.
- **.partitionBy("Ano", "Mes")**: Os dados são particionados por ano e mês, o que melhora a performance de consultas quando filtradas por essas colunas.

### Limpeza de Memória

In [0]:
import gc

# Coletar lixo após operações pesadas para liberar memória
gc.collect()

# Limpar todos os dados em cache
spark.catalog.clearCache()

###Evidências de Carga na Camada Gold (Delta)

In [0]:
%fs ls /mnt/lhdw/gold/vendas_delta/

path name size modificationTime dbfs:/mnt/lhdw/gold/vendas_delta/dim_categoria/ dim_categoria/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/dim_cliente/ dim_cliente/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/dim_fabricante/ dim_fabricante/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/dim_geografia/ dim_geografia/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/dim_produto/ dim_produto/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/dim_segmento/ dim_segmento/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas/ fato_vendas/ 0 0

In [0]:
%fs ls /mnt/lhdw/gold/vendas_delta/dim_categoria/

path name size modificationTime dbfs:/mnt/lhdw/gold/vendas_delta/dim_categoria/_delta_log/ _delta_log/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/dim_categoria/part-00000-cd87c664-4216-4121-9c07-2dd0c697e43a-c000.snappy.parquet part-00000-cd87c664-4216-4121-9c07-2dd0c697e43a-c000.snappy.parquet 948 1741958676000

In [0]:
%fs ls /mnt/lhdw/gold/vendas_delta/fato_vendas/Ano=2011/

path name size modificationTime dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas/Ano=2011/Mes=1/ Mes=1/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas/Ano=2011/Mes=10/ Mes=10/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas/Ano=2011/Mes=11/ Mes=11/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas/Ano=2011/Mes=12/ Mes=12/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas/Ano=2011/Mes=2/ Mes=2/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas/Ano=2011/Mes=3/ Mes=3/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas/Ano=2011/Mes=4/ Mes=4/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas/Ano=2011/Mes=5/ Mes=5/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas/Ano=2011/Mes=6/ Mes=6/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas/Ano=2011/Mes=7/ Mes=7/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas/Ano=2011/Mes=8/ Mes=8/ 0 0 dbfs:/mnt/lhdw/gold/vendas_delta/fato_vendas/Ano=2011/Mes=9/ Mes=9/ 0 0